## Technical Indicators List

All the indicators that https://pypi.org/project/stockstats/ supports

In [1]:
INDICATORS_LIST_ALL = ['high_5_sma','rsi','boll','macd','cr','wr','cci','tr','atr','dma','pdi','dx','adx','adxr','trix','tema','vr','mfi','vwma',
                   'chop','ppo','stochrsi','supertrend','aroon','close_75_z','ao'
                   ]

In [2]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import matplotlib.dates as mdates
#%matplotlib inline
import mplfinance as mpf # matplot.finance to plot candlesticks
import random
import itertools # iterators for efficient looping: https://docs.python.org/3/library/itertools.html 

from finrl.meta.preprocessor.yahoodownloader import YahooDownloader # a veces puede dar error al hacer fetch de la data porque no encuentra un stock o sus precios, o por la timezone
from finrl import config_tickers # config_tickers es una clase en la que se guardan en listas los nombres de cada stock para cada índice
from finrl.meta.preprocessor.preprocessors import FeatureEngineer, data_split
from finrl.meta.env_stock_trading.env_stocktrading import StockTradingEnv
from finrl.agents.stablebaselines3.models import DRLAgent
from stable_baselines3.common.logger import configure
from finrl.plot import backtest_stats, backtest_plot, get_daily_return, get_baseline

/Users/carolinaalbamaruganrubio/miniforge3/envs/ai4finance/lib/python3.10/site-packages/pyfolio/pos.py:26: UserWarning: Module "zipline.assets" not found; mutltipliers will not be applied to position notionals.
  warnings.warn(


In [3]:
TRAIN_START_DATE = '2010-01-01'
TRAIN_END_DATE = '2021-10-01'
TEST_START_DATE = '2021-10-01'
TEST_END_DATE = '2023-03-01'

In [4]:
stock = YahooDownloader(start_date = TRAIN_START_DATE,
                     end_date = TEST_END_DATE,
                     ticker_list = config_tickers.DOW_30_TICKER).fetch_data()

[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%*******

Shape of DataFrame:  (97013, 8)


In [5]:
stock # this DF contains all the stock price history from the train start date to the test end date, for every firm in the DJ30

date        open        high         low       close     volume  \
0      2010-01-04    7.622500    7.660714    7.585000    6.470742  493729600   
1      2010-01-04   56.630001   57.869999   56.560001   41.200779    5277400   
2      2010-01-04   40.810001   41.099998   40.389999   33.090446    6894300   
3      2010-01-04   55.720001   56.389999   54.799999   43.777554    6186700   
4      2010-01-04   57.650002   59.189999   57.509998   40.190216    7325600   
...           ...         ...         ...         ...         ...        ...   
97008  2023-02-28  482.670013  483.359985  473.920013  465.066864    3902100   
97009  2023-02-28  220.000000  221.770004  219.500000  217.824539    5385400   
97010  2023-02-28   38.700001   38.970001   38.549999   35.538387   16685300   
97011  2023-02-28   35.480000   35.779999   35.320000   32.750977    8847000   
97012  2023-02-28   47.000000   47.549999   46.983334   46.346085   18054000   

        tic  day  
0      AAPL    0  
1      AMGN    0  
2       AXP    0  
3        BA    0  
4       CAT    0  
...     ...  ...  
97008   UNH    1  
97009     V    1  
97010    VZ    1  
97011   WBA    1  
97012   WMT    1  

[97013 rows x 8 columns]

In [6]:
stock.day.describe()

count    97013.000000
mean         2.024131
std          1.398530
min          0.000000
25%          1.000000
50%          2.000000
75%          3.000000
max          4.000000
Name: day, dtype: float64

Stock symbols

In [7]:
tickers = stock.tic.unique()

We wanted to get:

In [8]:
print(np.reshape(config_tickers.DOW_30_TICKER, (len(config_tickers.DOW_30_TICKER))))
print("Number of firms in the index: ",len(config_tickers.DOW_30_TICKER))

['AXP' 'AMGN' 'AAPL' 'BA' 'CAT' 'CSCO' 'CVX' 'GS' 'HD' 'HON' 'IBM' 'INTC'
 'JNJ' 'KO' 'JPM' 'MCD' 'MMM' 'MRK' 'MSFT' 'NKE' 'PG' 'TRV' 'UNH' 'CRM'
 'VZ' 'V' 'WBA' 'WMT' 'DIS' 'DOW']
Number of firms in the index:  30


Creo que DOW es el DJIA, la media

But we got (because of the unavailable timezone or price data):

In [9]:
print(tickers) # stocks we have to train the agent
print("Number of firms downloaded: ",len(tickers))

['AAPL' 'AMGN' 'AXP' 'BA' 'CAT' 'CRM' 'CSCO' 'CVX' 'DIS' 'GS' 'HD' 'HON'
 'IBM' 'INTC' 'JNJ' 'JPM' 'KO' 'MCD' 'MMM' 'MRK' 'MSFT' 'NKE' 'PG' 'TRV'
 'UNH' 'V' 'VZ' 'WBA' 'WMT' 'DOW']
Number of firms downloaded:  30


## Agent 3

with following technical indicators:

In [10]:
# let's first take 4 technical indicators randomly from the supported indicators list
INDICATORS = [INDICATORS_LIST_ALL[i] for i in random.sample(range(len(INDICATORS_LIST_ALL)), 4)]

In [11]:
INDICATORS

['supertrend', 'high_5_sma', 'tema', 'chop']

In [12]:
# creamos instancia de FeatureEngineer indicando la configuración deseada para hacer el preproceso
fe = FeatureEngineer(
                    use_technical_indicator=True,
                    tech_indicator_list = INDICATORS,
                    use_vix=True, # AUN NO SE QUE ES ESTO
                    use_turbulence=True, # measures extreme asset price fluctuation --> if the turbulence index reaches a pre-defined threshold, the agent will halt buying action and start selling the holding shares gradually
                    user_defined_feature = False) # MIRA A VER QUÉ ERA DEFINIRSE UNA FEATURE (creo que es )

processed = fe.preprocess_data(stock)

Successfully added technical indicators


[*********************100%%**********************]  1 of 1 completed


Shape of DataFrame:  (3310, 8)
Successfully added vix
Successfully added turbulence index


Comentario: hay indicadores que pese a estar documentados como soportados en https://pypi.org/project/stockstats/, esta versión de código no los reconoce. Habrá que comprobar mediante más pruebas que todos los incluídos en la lista de todos los indicadores, estén soportados por esta versión. 

In [13]:
processed

date        open        high         low       close     volume  \
0      2010-01-04    7.622500    7.660714    7.585000    6.470742  493729600   
1      2010-01-04   56.630001   57.869999   56.560001   41.200779    5277400   
2      2010-01-04   40.810001   41.099998   40.389999   33.090446    6894300   
3      2010-01-04   55.720001   56.389999   54.799999   43.777554    6186700   
4      2010-01-04   57.650002   59.189999   57.509998   40.190216    7325600   
...           ...         ...         ...         ...         ...        ...   
95985  2023-02-27  488.769989  490.940002  481.959991  472.278229    3006200   
95986  2023-02-27  220.729996  221.440002  219.339996  218.230591    4255300   
95987  2023-02-27   38.990002   39.150002   38.630001   35.602482   14210900   
95988  2023-02-27   36.049999   36.080002   35.270000   32.621925    5580100   
95989  2023-02-27   47.570000   47.696667   46.886665   46.121086   16647300   

        tic  day  supertrend  high_5_sma        tema        chop        vix  \
0      AAPL    0   11.192773    7.660714    6.470742  104.382743  20.040001   
1      AMGN    0  107.222660   57.869999   41.200779   96.380575  20.040001   
2       AXP    0   64.773655   41.099998   33.090446   91.817878  20.040001   
3        BA    0   93.432337   56.389999   43.777554   78.473096  20.040001   
4       CAT    0  115.349346   59.189999   40.190216   91.912879  20.040001   
...     ...  ...         ...         ...         ...         ...        ...   
95985   UNH    0  528.902604  494.414001  472.307649   73.038919  20.950001   
95986     V    0  215.501733  221.592001  217.546533   46.661686  20.950001   
95987    VZ    0   48.206669   39.360000   35.438624  104.818863  20.950001   
95988   WBA    0   42.533680   36.282000   32.709818  121.678302  20.950001   
95989   WMT    0   50.711280   48.407333   46.078058   70.251888  20.950001   

       turbulence  
0        0.000000  
1        0.000000  
2        0.000000  
3        0.000000  
4        0.000000  
...           ...  
95985    7.163951  
95986    7.163951  
95987    7.163951  
95988    7.163951  
95989    7.163951  

[95990 rows x 14 columns]

In order to allow the Agent to have a consistent data structure to work with, we need to ensure that each stock has the same data range. This is necessary because not all stocks have data for every trading day due to holidays, stock-specific trading suspensions, or newly listed stocks. Therefore, we will establish a common data interval for each stock with day granularity and fill with 0 the (the more NaNs we have, the worst the performance will be). --> We can check this effect with other Stock Indices with less missing stock prices.

Convert the stock column to list

In [14]:
list_ticker = processed["tic"].unique().tolist()
print(list_ticker)
len(list_ticker)

['AAPL', 'AMGN', 'AXP', 'BA', 'CAT', 'CRM', 'CSCO', 'CVX', 'DIS', 'GS', 'HD', 'HON', 'IBM', 'INTC', 'JNJ', 'JPM', 'KO', 'MCD', 'MMM', 'MRK', 'MSFT', 'NKE', 'PG', 'TRV', 'UNH', 'V', 'VZ', 'WBA', 'WMT']


29

Create a list from the minimum to the maximum date and with the same granularity

In [15]:
list_date = list(pd.date_range(processed['date'].min(),processed['date'].max()).astype(str))
list_date

['2010-01-04',
 '2010-01-05',
 '2010-01-06',
 '2010-01-07',
 '2010-01-08',
 '2010-01-09',
 '2010-01-10',
 '2010-01-11',
 '2010-01-12',
 '2010-01-13',
 '2010-01-14',
 '2010-01-15',
 '2010-01-16',
 '2010-01-17',
 '2010-01-18',
 '2010-01-19',
 '2010-01-20',
 '2010-01-21',
 '2010-01-22',
 '2010-01-23',
 '2010-01-24',
 '2010-01-25',
 '2010-01-26',
 '2010-01-27',
 '2010-01-28',
 '2010-01-29',
 '2010-01-30',
 '2010-01-31',
 '2010-02-01',
 '2010-02-02',
 '2010-02-03',
 '2010-02-04',
 '2010-02-05',
 '2010-02-06',
 '2010-02-07',
 '2010-02-08',
 '2010-02-09',
 '2010-02-10',
 '2010-02-11',
 '2010-02-12',
 '2010-02-13',
 '2010-02-14',
 '2010-02-15',
 '2010-02-16',
 '2010-02-17',
 '2010-02-18',
 '2010-02-19',
 '2010-02-20',
 '2010-02-21',
 '2010-02-22',
 '2010-02-23',
 '2010-02-24',
 '2010-02-25',
 '2010-02-26',
 '2010-02-27',
 '2010-02-28',
 '2010-03-01',
 '2010-03-02',
 '2010-03-03',
 '2010-03-04',
 '2010-03-05',
 '2010-03-06',
 '2010-03-07',
 '2010-03-08',
 '2010-03-09',
 '2010-03-10',
 '2010-03-

Assign every day to each stock

In [16]:
combination = list(itertools.product(list_date,list_ticker))
combination

[('2010-01-04', 'AAPL'),
 ('2010-01-04', 'AMGN'),
 ('2010-01-04', 'AXP'),
 ('2010-01-04', 'BA'),
 ('2010-01-04', 'CAT'),
 ('2010-01-04', 'CRM'),
 ('2010-01-04', 'CSCO'),
 ('2010-01-04', 'CVX'),
 ('2010-01-04', 'DIS'),
 ('2010-01-04', 'GS'),
 ('2010-01-04', 'HD'),
 ('2010-01-04', 'HON'),
 ('2010-01-04', 'IBM'),
 ('2010-01-04', 'INTC'),
 ('2010-01-04', 'JNJ'),
 ('2010-01-04', 'JPM'),
 ('2010-01-04', 'KO'),
 ('2010-01-04', 'MCD'),
 ('2010-01-04', 'MMM'),
 ('2010-01-04', 'MRK'),
 ('2010-01-04', 'MSFT'),
 ('2010-01-04', 'NKE'),
 ('2010-01-04', 'PG'),
 ('2010-01-04', 'TRV'),
 ('2010-01-04', 'UNH'),
 ('2010-01-04', 'V'),
 ('2010-01-04', 'VZ'),
 ('2010-01-04', 'WBA'),
 ('2010-01-04', 'WMT'),
 ('2010-01-05', 'AAPL'),
 ('2010-01-05', 'AMGN'),
 ('2010-01-05', 'AXP'),
 ('2010-01-05', 'BA'),
 ('2010-01-05', 'CAT'),
 ('2010-01-05', 'CRM'),
 ('2010-01-05', 'CSCO'),
 ('2010-01-05', 'CVX'),
 ('2010-01-05', 'DIS'),
 ('2010-01-05', 'GS'),
 ('2010-01-05', 'HD'),
 ('2010-01-05', 'HON'),
 ('2010-01-05', 'IB

Merge with stock DF (potentially resulting in NaN values)

In [17]:
processed_full = pd.DataFrame(combination,columns=["date","tic"]).merge(processed,on=["date","tic"],how="left")

Remove non-trading days generated with the date range

In [18]:
processed_full = processed_full[processed_full['date'].isin(processed['date'])]

In [19]:
processed_full

date   tic        open        high         low       close  \
0       2010-01-04  AAPL    7.622500    7.660714    7.585000    6.470742   
1       2010-01-04  AMGN   56.630001   57.869999   56.560001   41.200779   
2       2010-01-04   AXP   40.810001   41.099998   40.389999   33.090446   
3       2010-01-04    BA   55.720001   56.389999   54.799999   43.777554   
4       2010-01-04   CAT   57.650002   59.189999   57.509998   40.190216   
...            ...   ...         ...         ...         ...         ...   
139282  2023-02-27   UNH  488.769989  490.940002  481.959991  472.278229   
139283  2023-02-27     V  220.729996  221.440002  219.339996  218.230591   
139284  2023-02-27    VZ   38.990002   39.150002   38.630001   35.602482   
139285  2023-02-27   WBA   36.049999   36.080002   35.270000   32.621925   
139286  2023-02-27   WMT   47.570000   47.696667   46.886665   46.121086   

             volume  day  supertrend  high_5_sma        tema        chop  \
0       493729600.0  0.0   11.192773    7.660714    6.470742  104.382743   
1         5277400.0  0.0  107.222660   57.869999   41.200779   96.380575   
2         6894300.0  0.0   64.773655   41.099998   33.090446   91.817878   
3         6186700.0  0.0   93.432337   56.389999   43.777554   78.473096   
4         7325600.0  0.0  115.349346   59.189999   40.190216   91.912879   
...             ...  ...         ...         ...         ...         ...   
139282    3006200.0  0.0  528.902604  494.414001  472.307649   73.038919   
139283    4255300.0  0.0  215.501733  221.592001  217.546533   46.661686   
139284   14210900.0  0.0   48.206669   39.360000   35.438624  104.818863   
139285    5580100.0  0.0   42.533680   36.282000   32.709818  121.678302   
139286   16647300.0  0.0   50.711280   48.407333   46.078058   70.251888   

              vix  turbulence  
0       20.040001    0.000000  
1       20.040001    0.000000  
2       20.040001    0.000000  
3       20.040001    0.000000  
4       20.040001    0.000000  
...           ...         ...  
139282  20.950001    7.163951  
139283  20.950001    7.163951  
139284  20.950001    7.163951  
139285  20.950001    7.163951  
139286  20.950001    7.163951  

[95990 rows x 14 columns]

In [20]:
len(processed_full.tic.unique())

29

In [21]:
processed_full.info()

<class 'pandas.core.frame.DataFrame'>
Index: 95990 entries, 0 to 139286
Data columns (total 14 columns):
 #   Column      Non-Null Count  Dtype  
---  ------      --------------  -----  
 0   date        95990 non-null  object 
 1   tic         95990 non-null  object 
 2   open        95990 non-null  float64
 3   high        95990 non-null  float64
 4   low         95990 non-null  float64
 5   close       95990 non-null  float64
 6   volume      95990 non-null  float64
 7   day         95990 non-null  float64
 8   supertrend  95990 non-null  float64
 9   high_5_sma  95990 non-null  float64
 10  tema        95990 non-null  float64
 11  chop        95990 non-null  float64
 12  vix         95990 non-null  float64
 13  turbulence  95990 non-null  float64
dtypes: float64(12), object(2)
memory usage: 11.0+ MB


In [22]:
processed_full.describe()

open          high           low         close        volume  \
count  95990.000000  95990.000000  95990.000000  95990.000000  9.599000e+04   
mean     102.224117    103.175365    101.253646     88.243726  1.995383e+07   
std       73.520545     74.279832     72.738958     70.607970  6.204278e+07   
min        6.870357      7.000000      6.794643      5.806765  3.054000e+05   
25%       47.470001     47.910000     47.020000     38.935157  4.003909e+06   
50%       83.498051     84.139999     82.830002     67.654839  7.250700e+06   
75%      138.477531    139.731735    137.169998    118.501167  1.498672e+07   
max      555.000000    558.099976    550.130005    540.800171  1.880998e+09   

                day    supertrend    high_5_sma          tema          chop  \
count  95990.000000  95990.000000  95990.000000  95990.000000  95990.000000   
mean       2.024471    100.243242    103.102538     88.243808    125.640480   
std        1.398649     71.285033     74.216049     70.611350     36.945210   
min        0.000000      6.685325      7.045357      5.850035      0.000000   
25%        1.000000     51.748250     47.854000     38.924814    102.932152   
50%        2.000000     81.492285     84.121000     67.653499    130.463458   
75%        3.000000    133.950494    139.601499    118.525984    153.309027   
max        4.000000    555.780714    553.847998    540.457274    217.589033   

                vix    turbulence  
count  95990.000000  95990.000000  
mean      18.721163     34.943610  
std        7.269653     43.065965  
min        9.140000      0.000000  
25%       13.630000     14.972837  
50%       16.875000     24.175921  
75%       21.760000     40.000378  
max       82.690002    652.619920

In this case, there are no nulls, but if there were we would need to fill them in the following way. 

In [23]:
processed_full = processed_full.sort_values(['date','tic']) # we need to sort bc of the data_split method CHECK SOURCE CODE 

processed_full = processed_full.fillna(0)

In [24]:
processed_full.describe()

open          high           low         close        volume  \
count  95990.000000  95990.000000  95990.000000  95990.000000  9.599000e+04   
mean     102.224117    103.175365    101.253646     88.243726  1.995383e+07   
std       73.520545     74.279832     72.738958     70.607970  6.204278e+07   
min        6.870357      7.000000      6.794643      5.806765  3.054000e+05   
25%       47.470001     47.910000     47.020000     38.935157  4.003909e+06   
50%       83.498051     84.139999     82.830002     67.654839  7.250700e+06   
75%      138.477531    139.731735    137.169998    118.501167  1.498672e+07   
max      555.000000    558.099976    550.130005    540.800171  1.880998e+09   

                day    supertrend    high_5_sma          tema          chop  \
count  95990.000000  95990.000000  95990.000000  95990.000000  95990.000000   
mean       2.024471    100.243242    103.102538     88.243808    125.640480   
std        1.398649     71.285033     74.216049     70.611350     36.945210   
min        0.000000      6.685325      7.045357      5.850035      0.000000   
25%        1.000000     51.748250     47.854000     38.924814    102.932152   
50%        2.000000     81.492285     84.121000     67.653499    130.463458   
75%        3.000000    133.950494    139.601499    118.525984    153.309027   
max        4.000000    555.780714    553.847998    540.457274    217.589033   

                vix    turbulence  
count  95990.000000  95990.000000  
mean      18.721163     34.943610  
std        7.269653     43.065965  
min        9.140000      0.000000  
25%       13.630000     14.972837  
50%       16.875000     24.175921  
75%       21.760000     40.000378  
max       82.690002    652.619920

In [25]:
large_value = 1e9

processed_full.replace([np.inf], large_value, inplace=True)

In [26]:
processed_full.describe()

open          high           low         close        volume  \
count  95990.000000  95990.000000  95990.000000  95990.000000  9.599000e+04   
mean     102.224117    103.175365    101.253646     88.243726  1.995383e+07   
std       73.520545     74.279832     72.738958     70.607970  6.204278e+07   
min        6.870357      7.000000      6.794643      5.806765  3.054000e+05   
25%       47.470001     47.910000     47.020000     38.935157  4.003909e+06   
50%       83.498051     84.139999     82.830002     67.654839  7.250700e+06   
75%      138.477531    139.731735    137.169998    118.501167  1.498672e+07   
max      555.000000    558.099976    550.130005    540.800171  1.880998e+09   

                day    supertrend    high_5_sma          tema          chop  \
count  95990.000000  95990.000000  95990.000000  95990.000000  95990.000000   
mean       2.024471    100.243242    103.102538     88.243808    125.640480   
std        1.398649     71.285033     74.216049     70.611350     36.945210   
min        0.000000      6.685325      7.045357      5.850035      0.000000   
25%        1.000000     51.748250     47.854000     38.924814    102.932152   
50%        2.000000     81.492285     84.121000     67.653499    130.463458   
75%        3.000000    133.950494    139.601499    118.525984    153.309027   
max        4.000000    555.780714    553.847998    540.457274    217.589033   

                vix    turbulence  
count  95990.000000  95990.000000  
mean      18.721163     34.943610  
std        7.269653     43.065965  
min        9.140000      0.000000  
25%       13.630000     14.972837  
50%       16.875000     24.175921  
75%       21.760000     40.000378  
max       82.690002    652.619920

Split Train and Test datasets

In [27]:
train = data_split(processed_full, TRAIN_START_DATE,TRAIN_END_DATE)
train

date   tic        open        high         low       close  \
0     2010-01-04  AAPL    7.622500    7.660714    7.585000    6.470742   
0     2010-01-04  AMGN   56.630001   57.869999   56.560001   41.200779   
0     2010-01-04   AXP   40.810001   41.099998   40.389999   33.090446   
0     2010-01-04    BA   55.720001   56.389999   54.799999   43.777554   
0     2010-01-04   CAT   57.650002   59.189999   57.509998   40.190216   
...          ...   ...         ...         ...         ...         ...   
2956  2021-09-30   UNH  401.489990  403.489990  390.459991  375.759766   
2956  2021-09-30     V  227.580002  228.789993  222.630005  218.139236   
2956  2021-09-30    VZ   54.500000   54.509998   54.000000   45.622715   
2956  2021-09-30   WBA   48.790001   48.930000   46.919998   40.519119   
2956  2021-09-30   WMT   46.880001   47.243332   46.416668   44.566532   

           volume  day  supertrend  high_5_sma        tema        chop  \
0     493729600.0  0.0   11.192773    7.660714    6.470742  104.382743   
0       5277400.0  0.0  107.222660   57.869999   41.200779   96.380575   
0       6894300.0  0.0   64.773655   41.099998   33.090446   91.817878   
0       6186700.0  0.0   93.432337   56.389999   43.777554   78.473096   
0       7325600.0  0.0  115.349346   59.189999   40.190216   91.912879   
...           ...  ...         ...         ...         ...         ...   
2956    3779900.0  3.0  366.259022  405.876001  377.412722   80.546612   
2956    7128500.0  3.0  237.458393  230.391998  219.417844   64.850197   
2956   18736600.0  3.0   65.550536   54.616000   45.716094  182.924639   
2956    6449400.0  3.0   53.897145   49.336000   40.940082  123.889038   
2956   22457700.0  3.0   50.712880   47.524667   44.599904   93.749105   

            vix  turbulence  
0     20.040001    0.000000  
0     20.040001    0.000000  
0     20.040001    0.000000  
0     20.040001    0.000000  
0     20.040001    0.000000  
...         ...         ...  
2956  23.139999   24.927229  
2956  23.139999   24.927229  
2956  23.139999   24.927229  
2956  23.139999   24.927229  
2956  23.139999   24.927229  

[85753 rows x 14 columns]

In [28]:
len(train.tic.unique())

29

In [29]:
train.tic.unique()

array(['AAPL', 'AMGN', 'AXP', 'BA', 'CAT', 'CRM', 'CSCO', 'CVX', 'DIS',
       'GS', 'HD', 'HON', 'IBM', 'INTC', 'JNJ', 'JPM', 'KO', 'MCD', 'MMM',
       'MRK', 'MSFT', 'NKE', 'PG', 'TRV', 'UNH', 'V', 'VZ', 'WBA', 'WMT'],
      dtype=object)

In [30]:
trade = data_split(processed_full, TEST_START_DATE,TEST_END_DATE)
trade

date   tic        open        high         low       close  \
0    2021-10-01  AAPL  141.899994  142.919998  139.110001  140.653503   
0    2021-10-01  AMGN  213.589996  214.610001  210.800003  195.822250   
0    2021-10-01   AXP  168.500000  175.119995  168.479996  167.727432   
0    2021-10-01    BA  222.850006  226.720001  220.600006  226.000000   
0    2021-10-01   CAT  192.899994  195.869995  191.240005  183.513977   
..          ...   ...         ...         ...         ...         ...   
352  2023-02-27   UNH  488.769989  490.940002  481.959991  472.278229   
352  2023-02-27     V  220.729996  221.440002  219.339996  218.230591   
352  2023-02-27    VZ   38.990002   39.150002   38.630001   35.602482   
352  2023-02-27   WBA   36.049999   36.080002   35.270000   32.621925   
352  2023-02-27   WMT   47.570000   47.696667   46.886665   46.121086   

         volume  day  supertrend  high_5_sma        tema        chop  \
0    94639600.0  4.0  151.962212  144.492001  140.060804   52.599639   
0     2629400.0  4.0  178.648656  215.557999  195.572014  129.938977   
0     3956000.0  4.0  152.435852  175.300000  165.806740   67.869157   
0     9113600.0  4.0  209.674360  227.198001  224.813103   49.304866   
0     3695500.0  4.0  227.936156  199.956000  183.268493   83.959205   
..          ...  ...         ...         ...         ...         ...   
352   3006200.0  0.0  528.902604  494.414001  472.307649   73.038919   
352   4255300.0  0.0  215.501733  221.592001  217.546533   46.661686   
352  14210900.0  0.0   48.206669   39.360000   35.438624  104.818863   
352   5580100.0  0.0   42.533680   36.282000   32.709818  121.678302   
352  16647300.0  0.0   50.711280   48.407333   46.078058   70.251888   

           vix  turbulence  
0    21.100000  120.031019  
0    21.100000  120.031019  
0    21.100000  120.031019  
0    21.100000  120.031019  
0    21.100000  120.031019  
..         ...         ...  
352  20.950001    7.163951  
352  20.950001    7.163951  
352  20.950001    7.163951  
352  20.950001    7.163951  
352  20.950001    7.163951  

[10237 rows x 14 columns]

In [31]:
train_length = len(train)
trade_length = len(trade)
print("Number of training samples: ", train_length)
print("Number of testing samples", trade_length)

Number of training samples:  85753
Number of testing samples 10237


In [32]:
train.tail()

date  tic        open        high         low       close  \
2956  2021-09-30  UNH  401.489990  403.489990  390.459991  375.759766   
2956  2021-09-30    V  227.580002  228.789993  222.630005  218.139236   
2956  2021-09-30   VZ   54.500000   54.509998   54.000000   45.622715   
2956  2021-09-30  WBA   48.790001   48.930000   46.919998   40.519119   
2956  2021-09-30  WMT   46.880001   47.243332   46.416668   44.566532   

          volume  day  supertrend  high_5_sma        tema        chop  \
2956   3779900.0  3.0  366.259022  405.876001  377.412722   80.546612   
2956   7128500.0  3.0  237.458393  230.391998  219.417844   64.850197   
2956  18736600.0  3.0   65.550536   54.616000   45.716094  182.924639   
2956   6449400.0  3.0   53.897145   49.336000   40.940082  123.889038   
2956  22457700.0  3.0   50.712880   47.524667   44.599904   93.749105   

            vix  turbulence  
2956  23.139999   24.927229  
2956  23.139999   24.927229  
2956  23.139999   24.927229  
2956  23.139999   24.927229  
2956  23.139999   24.927229

In [33]:
trade.head()

date   tic        open        high         low       close  \
0  2021-10-01  AAPL  141.899994  142.919998  139.110001  140.653503   
0  2021-10-01  AMGN  213.589996  214.610001  210.800003  195.822250   
0  2021-10-01   AXP  168.500000  175.119995  168.479996  167.727432   
0  2021-10-01    BA  222.850006  226.720001  220.600006  226.000000   
0  2021-10-01   CAT  192.899994  195.869995  191.240005  183.513977   

       volume  day  supertrend  high_5_sma        tema        chop   vix  \
0  94639600.0  4.0  151.962212  144.492001  140.060804   52.599639  21.1   
0   2629400.0  4.0  178.648656  215.557999  195.572014  129.938977  21.1   
0   3956000.0  4.0  152.435852  175.300000  165.806740   67.869157  21.1   
0   9113600.0  4.0  209.674360  227.198001  224.813103   49.304866  21.1   
0   3695500.0  4.0  227.936156  199.956000  183.268493   83.959205  21.1   

   turbulence  
0  120.031019  
0  120.031019  
0  120.031019  
0  120.031019  
0  120.031019

Since we need to set the parameters for the environment functions, we need to compute the stock dimension and state space.

In [34]:
# Number of unique stocks used for the training 
stock_dimension = len(train.tic.unique())
# {balance, close price, shares, N-technical indicators}
# Balance will occupy 1 input node, and it is computed as: balance = balance (t) − amount of money we pay to buy shares + amount of money we receive to sell shares
# We will have N input nodes for the stock prices and N additional input nodes to indicate the current number of shares for each stock --> 2*N
# we will have one node for every technical indicator for every stock --> M indicators * N stocks
state_space = 1 + 2*stock_dimension + len(INDICATORS)*stock_dimension
print(f"Stock Dimension (Number of different companies in which we want to invest initially): {stock_dimension}, State Space (Number of input nodes to feed to the network): {state_space}")

Stock Dimension (Number of different companies in which we want to invest initially): 29, State Space (Number of input nodes to feed to the network): 175


Most of the trading companies demand trading commissions or costs. Here, we will simulate a buying and selling commission of 0,1% for each transaction. We will assume the user starts having no shares of any stock. Let's also assume we have 1.000.000 dollars to invest with. We will also define a parameter that sets the maximum amount of shares to trade, h_max. It is interesting to set the scaling reward or gamma (importance we give to the future reward), so that we specify if we give more importance to the short or long term. We could modify these parameters, if needed.

In [35]:
buy_cost_list = sell_cost_list = [0.001] * stock_dimension
num_stock_shares = [0] * stock_dimension
h_max = 100
initial_amount = 1000000
gamma = 1e-4 # we are assuming we want to get the highest return in the short term, preventing ourselves from the risk and uncertainty caused by external factors in the long term

HAZ PRUEBAS CON UN GAMMA MÁS ALTO

Let's set the configuration that will be passed to the Environment class

In [36]:
env_kwargs = {
    "hmax": h_max,
    "initial_amount": initial_amount, 
    "num_stock_shares": num_stock_shares,
    "buy_cost_pct": buy_cost_list,
    "sell_cost_pct": sell_cost_list,
    "state_space": state_space,
    "stock_dim": stock_dimension,
    "tech_indicator_list": INDICATORS,
    "action_space": stock_dimension,
    "reward_scaling": gamma
}

Let's create the Stock Trading Environment!

In [37]:
e_train_gym = StockTradingEnv(df = train, **env_kwargs) # creates instance of the Environment class
print("Environment class type", type(e_train_gym))
env_train, _ = e_train_gym.get_sb_env() # resets the environment and converts the initial environment into a DummyVecEnv instance
print("External Environment class type: ", type(env_train))

Environment class type <class 'finrl.meta.env_stock_trading.env_stocktrading.StockTradingEnv'>
External Environment class type:  <class 'stable_baselines3.common.vec_env.dummy_vec_env.DummyVecEnv'>


Since we will use different RL algorithms, let's set some flags:

In [38]:
if_using_a2c = True
if_using_ddpg = True
if_using_ppo = True
if_using_td3 = True
if_using_sac = True

Let's create the Deep Reinforcement Learning Agent!

podríamos runear todos los ind (p.e. 3 o 4 ind) y con los mejores, cambiar el resto de parametros (fechas, gamma,...)

# A2C

In [39]:
agent = DRLAgent(env = env_train) # creates Agent instance
model_a2c = agent.get_model("a2c") # gets stablebaselines3 model  

if if_using_a2c: # where to store the results
  # set up logger
  tmp_path = 'resultadosTFG' + '/set_3' + '/a2c'
  new_logger_a2c = configure(tmp_path, ["stdout", "csv", "tensorboard"])
  # Set new logger
  model_a2c.set_logger(new_logger_a2c)

{'n_steps': 5, 'ent_coef': 0.01, 'learning_rate': 0.0007}
Using cpu device
Logging to resultadosTFG/set_3/a2c


Let's train the agent!

In [40]:
trained_a2c = agent.train_model(model=model_a2c, 
                             tb_log_name='a2c',
                             total_timesteps=50000) if if_using_a2c else None

--------------------------------------
| time/                 |            |
|    fps                | 186        |
|    iterations         | 100        |
|    time_elapsed       | 2          |
|    total_timesteps    | 500        |
| train/                |            |
|    entropy_loss       | -41.1      |
|    explained_variance | 0.777      |
|    learning_rate      | 0.0007     |
|    n_updates          | 99         |
|    policy_loss        | -73.2      |
|    reward             | -0.5617495 |
|    std                | 0.998      |
|    value_loss         | 3.11       |
--------------------------------------
---------------------------------------
| time/                 |             |
|    fps                | 187         |
|    iterations         | 200         |
|    time_elapsed       | 5           |
|    total_timesteps    | 1000        |
| train/                |             |
|    entropy_loss       | -41         |
|    explained_variance | 0.0287      |
|    learning_ra

In [41]:
trained_a2c.policy

ActorCriticPolicy(
  (features_extractor): FlattenExtractor(
    (flatten): Flatten(start_dim=1, end_dim=-1)
  )
  (pi_features_extractor): FlattenExtractor(
    (flatten): Flatten(start_dim=1, end_dim=-1)
  )
  (vf_features_extractor): FlattenExtractor(
    (flatten): Flatten(start_dim=1, end_dim=-1)
  )
  (mlp_extractor): MlpExtractor(
    (policy_net): Sequential(
      (0): Linear(in_features=175, out_features=64, bias=True)
      (1): Tanh()
      (2): Linear(in_features=64, out_features=64, bias=True)
      (3): Tanh()
    )
    (value_net): Sequential(
      (0): Linear(in_features=175, out_features=64, bias=True)
      (1): Tanh()
      (2): Linear(in_features=64, out_features=64, bias=True)
      (3): Tanh()
    )
  )
  (action_net): Linear(in_features=64, out_features=29, bias=True)
  (value_net): Linear(in_features=64, out_features=1, bias=True)
)

Let's see the learning progress of the agent

In [42]:
learning_process = pd.read_csv("resultadosTFG/set_3/a2c/progress.csv")
learning_process

time/time_elapsed  train/n_updates  train/learning_rate  time/iterations  \
0                   2               99               0.0007              100   
1                   5              199               0.0007              200   
2                   7              299               0.0007              300   
3                  10              399               0.0007              400   
4                  13              499               0.0007              500   
..                ...              ...                  ...              ...   
95                289             9599               0.0007             9600   
96                292             9699               0.0007             9700   
97                295             9799               0.0007             9800   
98                297             9899               0.0007             9900   
99                300             9999               0.0007            10000   

    train/explained_variance  train/value_loss  time/fps  \
0               7.765677e-01          3.111393       186   
1               2.874625e-02          1.246640       187   
2              -5.824172e-02          7.255102       189   
3               0.000000e+00         36.845776       191   
4               0.000000e+00         44.979965       192   
..                       ...               ...       ...   
95             -1.192093e-07          4.934962       165   
96              0.000000e+00          0.486296       165   
97             -1.192093e-07         38.624268       166   
98             -1.902014e-01          0.860302       166   
99             -1.192093e-07         18.000393       166   

    time/total_timesteps  train/std  train/entropy_loss  train/policy_loss  \
0                    500   0.997855          -41.086037         -73.204689   
1                   1000   0.996522          -41.044357          -2.585628   
2                   1500   0.995351          -41.011528         -25.487370   
3                   2000   0.995361          -41.009064        -219.317535   
4                   2500   0.994315          -40.967140        -224.830444   
..                   ...        ...                 ...                ...   
95                 48000   1.058674          -42.737370          58.710640   
96                 48500   1.059072          -42.745018          10.928807   
97                 49000   1.060657          -42.778530        -248.614700   
98                 49500   1.061098          -42.797749         -17.254707   
99                 50000   1.061492          -42.802814         135.945190   

    train/reward  
0      -0.561750  
1      -0.525970  
2      -3.019127  
3       1.378944  
4      -1.422159  
..           ...  
95     -1.899911  
96     -0.370512  
97     -0.567594  
98     -1.120894  
99     -4.924271  

[100 rows x 12 columns]

Plot the training results

In [43]:
def plot_metrics(df, n_rows, n_cols):
    fig, axes = plt.subplots(nrows=n_rows, ncols=n_cols, figsize=(5 * n_cols, 5 * n_rows))
    axes = axes.flatten()  # Flatten the array of axes if more than one row or column

    # List of tuples containing (y-axis, title)
    metrics = [
        ('train/reward', 'Reward'),
        ('train/policy_loss', 'Policy Loss'),
        ('train/std', 'Standard Deviation'),
        ('train/n_updates', 'Number of Updates'),
        ('train/value_loss', 'Value Loss'),
        ('time/fps', 'Frames Per Second'),
        ('train/explained_variance', 'Explained Variance'),
        ('train/entropy_loss', 'Entropy Loss')
    ]

    # Plot each metric
    for ax, (metric, title) in zip(axes, metrics):
        ax.plot(df['time/total_timesteps'], df[metric], label=title)
        ax.set_xlabel('Total Timesteps')
        ax.set_ylabel(title)
        ax.set_title(title)
        ax.grid(True)
        ax.legend()

    plt.tight_layout()
    plt.savefig(f'resultadosTFG/set_3/a2c/trainingStatsResults.png')
    plt.close()

df = learning_process
plot_metrics(df, n_rows=4, n_cols=2)  # Modify n_rows and n_cols as needed


The agent is not learning very well... 

Podríamos hacer una tabla resumen de todos los algos y pones cuántos steps han sido necesarios, la LR de cada uno, etc

# PPO

Set PPO parameters and set the logger

In [44]:
agent = DRLAgent(env = env_train)
PPO_PARAMS = {
    "n_steps": 2048,
    "ent_coef": 0.01,
    "learning_rate": 0.00025,
    "batch_size": 128,
}
model_ppo = agent.get_model("ppo",model_kwargs = PPO_PARAMS)

if if_using_ppo:
  # set up logger
  tmp_path = 'resultadosTFG' + '/set_3' + '/ppo'
  new_logger_ppo = configure(tmp_path, ["stdout", "csv", "tensorboard"])
  # Set new logger
  model_ppo.set_logger(new_logger_ppo)

{'n_steps': 2048, 'ent_coef': 0.01, 'learning_rate': 0.00025, 'batch_size': 128}
Using cpu device
Logging to resultadosTFG/set_3/ppo


Train PPO

In [45]:
trained_ppo = agent.train_model(model=model_ppo, 
                             tb_log_name='ppo',
                             total_timesteps=50000) if if_using_ppo else None

---------------------------------
| time/              |          |
|    fps             | 218      |
|    iterations      | 1        |
|    time_elapsed    | 9        |
|    total_timesteps | 2048     |
| train/             |          |
|    reward          | 0.502884 |
---------------------------------
-----------------------------------------
| time/                   |             |
|    fps                  | 217         |
|    iterations           | 2           |
|    time_elapsed         | 18          |
|    total_timesteps      | 4096        |
| train/                  |             |
|    approx_kl            | 0.020100383 |
|    clip_fraction        | 0.233       |
|    clip_range           | 0.2         |
|    entropy_loss         | -41.2       |
|    explained_variance   | -0.00961    |
|    learning_rate        | 0.00025     |
|    loss                 | 5.54        |
|    n_updates            | 10          |
|    policy_gradient_loss | -0.0227     |
|    reward           

In [46]:
trained_ppo.policy

ActorCriticPolicy(
  (features_extractor): FlattenExtractor(
    (flatten): Flatten(start_dim=1, end_dim=-1)
  )
  (pi_features_extractor): FlattenExtractor(
    (flatten): Flatten(start_dim=1, end_dim=-1)
  )
  (vf_features_extractor): FlattenExtractor(
    (flatten): Flatten(start_dim=1, end_dim=-1)
  )
  (mlp_extractor): MlpExtractor(
    (policy_net): Sequential(
      (0): Linear(in_features=175, out_features=64, bias=True)
      (1): Tanh()
      (2): Linear(in_features=64, out_features=64, bias=True)
      (3): Tanh()
    )
    (value_net): Sequential(
      (0): Linear(in_features=175, out_features=64, bias=True)
      (1): Tanh()
      (2): Linear(in_features=64, out_features=64, bias=True)
      (3): Tanh()
    )
  )
  (action_net): Linear(in_features=64, out_features=29, bias=True)
  (value_net): Linear(in_features=64, out_features=1, bias=True)
)

Let's see the learning progress of the agent

In [47]:
learning_process = pd.read_csv("resultadosTFG/set_3/ppo/progress.csv")
learning_process

time/total_timesteps  time/time_elapsed  time/iterations  time/fps  \
0                   2048                  9                1       218   
1                   4096                 18                2       217   
2                   6144                 28                3       216   
3                   8192                 37                4       215   
4                  10240                 47                5       215   
5                  12288                 57                6       215   
6                  14336                 67                7       213   
7                  16384                 77                8       212   
8                  18432                 87                9       211   
9                  20480                 97               10       209   
10                 22528                107               11       209   
11                 24576                117               12       208   
12                 26624                127               13       208   
13                 28672                137               14       208   
14                 30720                148               15       207   
15                 32768                158               16       206   
16                 34816                167               17       207   
17                 36864                177               18       207   
18                 38912                186               19       208   
19                 40960                196               20       208   
20                 43008                205               21       208   
21                 45056                215               22       208   
22                 47104                225               23       209   
23                 49152                234               24       209   
24                 51200                244               25       209   

    train/reward  train/clip_fraction  train/n_updates  train/learning_rate  \
0       0.502884                  NaN              NaN                  NaN   
1      -0.737988             0.233447             10.0              0.00025   
2       1.747645             0.177393             20.0              0.00025   
3       0.670501             0.156543             30.0              0.00025   
4      -1.731412             0.172266             40.0              0.00025   
5       0.559893             0.197754             50.0              0.00025   
6       3.162547             0.194922             60.0              0.00025   
7      -2.520518             0.174951             70.0              0.00025   
8       1.107652             0.211475             80.0              0.00025   
9       2.053711             0.188965             90.0              0.00025   
10      0.022823             0.165967            100.0              0.00025   
11      0.636901             0.229395            110.0              0.00025   
12     -0.153610             0.223535            120.0              0.00025   
13      4.500647             0.242627            130.0              0.00025   
14      1.536679             0.240283            140.0              0.00025   
15      0.352011             0.215039            150.0              0.00025   
16     -3.551043             0.230078            160.0              0.00025   
17     -3.733875             0.210547            170.0              0.00025   
18     -0.979960             0.225635            180.0              0.00025   
19     -2.231954             0.180566            190.0              0.00025   
20     -0.060124             0.229248            200.0              0.00025   
21      0.142946             0.212305            210.0              0.00025   
22      0.994505             0.253223            220.0              0.00025   
23     -0.075111             0.211035            230.0              0.00025   
24      1.250264             0.334766            240.0              0.00025   

    train/approx_kl  tra

Plot the training results

In [48]:
def plot_metrics(df, n_rows, n_cols):
    fig, axes = plt.subplots(nrows=n_rows, ncols=n_cols, figsize=(5 * n_cols, 5 * n_rows))
    axes = axes.flatten()  # Flatten the array of axes if more than one row or column

    metrics = [
        ('train/reward', 'Reward'),
        ('train/loss', 'Loss'),
        ('train/std', 'Standard Deviation'),
        ('train/approx_kl', 'approximate Kullback-Leibler divergence'),
        ('train/clip_fraction', 'Clip Fraction'),
        ('train/clip_range', 'Clip Range'),
        ('train/explained_variance', 'Explained Variance'),
        ('train/value_loss', 'Value Loss'),
        ('train/policy_gradient_loss', 'Policy Gradient Loss'),
        ('train/entropy_loss', 'Entropy Loss')
    ]

    # Plot each metric
    for ax, (metric, title) in zip(axes, metrics):
        ax.plot(df['time/total_timesteps'], df[metric], label=title)
        ax.set_xlabel('Total Timesteps')
        ax.set_ylabel(title)
        ax.set_title(title)
        ax.grid(True)
        ax.legend()

    plt.tight_layout()
    plt.savefig(f'resultadosTFG/set_3/ppo/trainingStatsResults.png')
    plt.close()

df = learning_process
plot_metrics(df, n_rows=5, n_cols=2)  # Modify n_rows and n_cols as needed

# DDPG

Create the agent and set the logger

In [49]:
agent = DRLAgent(env = env_train)
model_ddpg = agent.get_model("ddpg")

if if_using_ddpg:
  # set up logger
  tmp_path = 'resultadosTFG' + '/set_3' + '/ddpg'
  new_logger_ddpg = configure(tmp_path, ["stdout", "csv", "tensorboard"])
  # Set new logger
  model_ddpg.set_logger(new_logger_ddpg)

{'batch_size': 128, 'buffer_size': 50000, 'learning_rate': 0.001}
Using cpu device
Logging to resultadosTFG/set_3/ddpg


Train the agent

In [50]:
trained_ddpg = agent.train_model(model=model_ddpg, 
                             tb_log_name='ddpg',
                             total_timesteps=50000) if if_using_ddpg else None

day: 2956, episode: 40
begin_total_asset: 1000000.00
end_total_asset: 3855138.18
total_reward: 2855138.18
total_cost: 999.00
total_trades: 47296
Sharpe: 0.719
----------------------------------
| time/              |           |
|    episodes        | 4         |
|    fps             | 111       |
|    time_elapsed    | 106       |
|    total_timesteps | 11828     |
| train/             |           |
|    actor_loss      | -19       |
|    critic_loss     | 2.56e+03  |
|    learning_rate   | 0.001     |
|    n_updates       | 8871      |
|    reward          | -6.842287 |
----------------------------------
----------------------------------
| time/              |           |
|    episodes        | 8         |
|    fps             | 102       |
|    time_elapsed    | 231       |
|    total_timesteps | 23656     |
| train/             |           |
|    actor_loss      | -25.5     |
|    critic_loss     | 8.12      |
|    learning_rate   | 0.001     |
|    n_updates       | 20699     |
|

In [51]:
trained_ddpg.policy

TD3Policy(
  (actor): Actor(
    (features_extractor): FlattenExtractor(
      (flatten): Flatten(start_dim=1, end_dim=-1)
    )
    (mu): Sequential(
      (0): Linear(in_features=175, out_features=400, bias=True)
      (1): ReLU()
      (2): Linear(in_features=400, out_features=300, bias=True)
      (3): ReLU()
      (4): Linear(in_features=300, out_features=29, bias=True)
      (5): Tanh()
    )
  )
  (actor_target): Actor(
    (features_extractor): FlattenExtractor(
      (flatten): Flatten(start_dim=1, end_dim=-1)
    )
    (mu): Sequential(
      (0): Linear(in_features=175, out_features=400, bias=True)
      (1): ReLU()
      (2): Linear(in_features=400, out_features=300, bias=True)
      (3): ReLU()
      (4): Linear(in_features=300, out_features=29, bias=True)
      (5): Tanh()
    )
  )
  (critic): ContinuousCritic(
    (features_extractor): FlattenExtractor(
      (flatten): Flatten(start_dim=1, end_dim=-1)
    )
    (qf0): Sequential(
      (0): Linear(in_features=204, out_

Let's see the learning progress of the agent 

In [52]:
learning_process = pd.read_csv("resultadosTFG/set_3/ddpg/progress.csv")
learning_process

time/time_elapsed  train/n_updates  train/learning_rate  train/critic_loss  \
0                106             8871                0.001        2556.083194   
1                231            20699                0.001           8.116410   
2                350            32527                0.001           3.583010   
3                476            44355                0.001           2.651771   

   time/fps  train/actor_loss  time/total_timesteps  time/episodes  \
0       111        -19.007332                 11828              4   
1       102        -25.502018                 23656              8   
2       101        -19.271726                 35484             12   
3        99        -16.036260                 47312             16   

   train/reward  
0     -6.842287  
1     -6.842287  
2     -6.842287  
3     -6.842287

Plot the results of the training

In [53]:
def plot_metrics(df, n_rows, n_cols):
    fig, axes = plt.subplots(nrows=n_rows, ncols=n_cols, figsize=(5 * n_cols, 5 * n_rows))
    axes = axes.flatten()  # Flatten the array of axes if more than one row or column

    metrics = [
        ('train/reward', 'Reward'),
        ('train/actor_loss', 'Actor Loss'),
        ('train/n_updates', 'Number of Updates'),
        ('train/critic_loss', 'Critic Loss')
    ]

    # Plot each metric
    for ax, (metric, title) in zip(axes, metrics):
        ax.plot(df['time/total_timesteps'], df[metric], label=title)
        ax.set_xlabel('Total Timesteps')
        ax.set_ylabel(title)
        ax.set_title(title)
        ax.grid(True)
        ax.legend()

    plt.tight_layout()
    plt.savefig(f'resultadosTFG/set_3/ddpg/trainingStatsResults.png')
    plt.close()

df = learning_process
plot_metrics(df, n_rows=4, n_cols=1)  # Modify n_rows and n_cols as needed

# TD3

Create the agent and set the logger

In [54]:
agent = DRLAgent(env = env_train)
TD3_PARAMS = {"batch_size": 100, 
              "buffer_size": 1000000, 
              "learning_rate": 0.001}

model_td3 = agent.get_model("td3",model_kwargs = TD3_PARAMS)

if if_using_td3:
  # set up logger
  tmp_path = 'resultadosTFG' + '/set_3' + '/td3'
  new_logger_td3 = configure(tmp_path, ["stdout", "csv", "tensorboard"])
  # Set new logger
  model_td3.set_logger(new_logger_td3)

{'batch_size': 100, 'buffer_size': 1000000, 'learning_rate': 0.001}
Using cpu device
Logging to resultadosTFG/set_3/td3


/Users/carolinaalbamaruganrubio/miniforge3/envs/ai4finance/lib/python3.10/site-packages/stable_baselines3/common/buffers.py:241: UserWarning: This system does not have apparently enough memory to store the complete replay buffer 1.52GB > 1.36GB
  warnings.warn(


Train TD3

In [55]:
trained_td3 = agent.train_model(model=model_td3, 
                             tb_log_name='td3',
                             total_timesteps=50000) if if_using_td3 else None

-----------------------------------
| time/              |            |
|    episodes        | 4          |
|    fps             | 126        |
|    time_elapsed    | 93         |
|    total_timesteps | 11828      |
| train/             |            |
|    actor_loss      | -48.2      |
|    critic_loss     | 152        |
|    learning_rate   | 0.001      |
|    n_updates       | 8871       |
|    reward          | -5.9681287 |
-----------------------------------
day: 2956, episode: 60
begin_total_asset: 1000000.00
end_total_asset: 3984656.01
total_reward: 2984656.01
total_cost: 1241.23
total_trades: 53224
Sharpe: 0.757
-----------------------------------
| time/              |            |
|    episodes        | 8          |
|    fps             | 117        |
|    time_elapsed    | 201        |
|    total_timesteps | 23656      |
| train/             |            |
|    actor_loss      | -29.4      |
|    critic_loss     | 22.9       |
|    learning_rate   | 0.001      |
|    n_updat

In [56]:
trained_td3.policy

TD3Policy(
  (actor): Actor(
    (features_extractor): FlattenExtractor(
      (flatten): Flatten(start_dim=1, end_dim=-1)
    )
    (mu): Sequential(
      (0): Linear(in_features=175, out_features=400, bias=True)
      (1): ReLU()
      (2): Linear(in_features=400, out_features=300, bias=True)
      (3): ReLU()
      (4): Linear(in_features=300, out_features=29, bias=True)
      (5): Tanh()
    )
  )
  (actor_target): Actor(
    (features_extractor): FlattenExtractor(
      (flatten): Flatten(start_dim=1, end_dim=-1)
    )
    (mu): Sequential(
      (0): Linear(in_features=175, out_features=400, bias=True)
      (1): ReLU()
      (2): Linear(in_features=400, out_features=300, bias=True)
      (3): ReLU()
      (4): Linear(in_features=300, out_features=29, bias=True)
      (5): Tanh()
    )
  )
  (critic): ContinuousCritic(
    (features_extractor): FlattenExtractor(
      (flatten): Flatten(start_dim=1, end_dim=-1)
    )
    (qf0): Sequential(
      (0): Linear(in_features=204, out_

Let's see agent's learning process

In [57]:
learning_process = pd.read_csv("resultadosTFG/set_3/td3/progress.csv")
learning_process

time/time_elapsed  train/n_updates  train/learning_rate  train/critic_loss  \
0                 93             8871                0.001         151.681542   
1                201            20699                0.001          22.941467   
2                312            32527                0.001          10.156706   
3                423            44355                0.001           8.826827   

   time/fps  train/actor_loss  time/total_timesteps  time/episodes  \
0       126        -48.167887                 11828              4   
1       117        -29.364729                 23656              8   
2       113        -20.159106                 35484             12   
3       111        -12.807354                 47312             16   

   train/reward  
0     -5.968129  
1     -5.968129  
2     -5.968129  
3     -5.968129

Plot training results

In [58]:
def plot_metrics(df, n_rows, n_cols):
    fig, axes = plt.subplots(nrows=n_rows, ncols=n_cols, figsize=(5 * n_cols, 5 * n_rows))
    axes = axes.flatten()  # Flatten the array of axes if more than one row or column

    metrics = [
        ('train/reward', 'Reward'),
        ('train/actor_loss', 'Actor Loss'),
        ('train/n_updates', 'Number of Updates'),
        ('train/critic_loss', 'Critic Loss')
    ]

    # Plot each metric
    for ax, (metric, title) in zip(axes, metrics):
        ax.plot(df['time/total_timesteps'], df[metric], label=title)
        ax.set_xlabel('Total Timesteps')
        ax.set_ylabel(title)
        ax.set_title(title)
        ax.grid(True)
        ax.legend()

    plt.tight_layout()
    plt.savefig(f'resultadosTFG/set_3/td3/trainingStatsResults.png')
    plt.close()

df = learning_process
plot_metrics(df, n_rows=4, n_cols=1)  # Modify n_rows and n_cols as needed

# SAC

Create the agent, set parameters for training, and set logger

In [59]:
agent = DRLAgent(env = env_train)
SAC_PARAMS = {
    "batch_size": 128,
    "buffer_size": 100000,
    "learning_rate": 0.0001,
    "learning_starts": 100,
    "ent_coef": "auto_0.1",
}

model_sac = agent.get_model("sac",model_kwargs = SAC_PARAMS)

if if_using_sac:
  # set up logger
  tmp_path = 'resultadosTFG' + '/set_3' + '/sac'
  new_logger_sac = configure(tmp_path, ["stdout", "csv", "tensorboard"])
  # Set new logger
  model_sac.set_logger(new_logger_sac)

{'batch_size': 128, 'buffer_size': 100000, 'learning_rate': 0.0001, 'learning_starts': 100, 'ent_coef': 'auto_0.1'}
Using cpu device
Logging to resultadosTFG/set_3/sac


Train SAC

In [60]:
trained_sac = agent.train_model(model=model_sac, 
                             tb_log_name='sac',
                             total_timesteps=50000) if if_using_sac else None

-----------------------------------
| time/              |            |
|    episodes        | 4          |
|    fps             | 78         |
|    time_elapsed    | 151        |
|    total_timesteps | 11828      |
| train/             |            |
|    actor_loss      | 1.23e+03   |
|    critic_loss     | 97.3       |
|    ent_coef        | 0.239      |
|    ent_coef_loss   | -15.6      |
|    learning_rate   | 0.0001     |
|    n_updates       | 11727      |
|    reward          | -6.3160205 |
-----------------------------------
day: 2956, episode: 80
begin_total_asset: 1000000.00
end_total_asset: 4206787.36
total_reward: 3206787.36
total_cost: 10443.85
total_trades: 48969
Sharpe: 0.765
---------------------------------
| time/              |          |
|    episodes        | 8        |
|    fps             | 74       |
|    time_elapsed    | 318      |
|    total_timesteps | 23656    |
| train/             |          |
|    actor_loss      | 520      |
|    critic_loss     | 125 

In [61]:
trained_sac.policy

SACPolicy(
  (actor): Actor(
    (features_extractor): FlattenExtractor(
      (flatten): Flatten(start_dim=1, end_dim=-1)
    )
    (latent_pi): Sequential(
      (0): Linear(in_features=175, out_features=256, bias=True)
      (1): ReLU()
      (2): Linear(in_features=256, out_features=256, bias=True)
      (3): ReLU()
    )
    (mu): Linear(in_features=256, out_features=29, bias=True)
    (log_std): Linear(in_features=256, out_features=29, bias=True)
  )
  (critic): ContinuousCritic(
    (features_extractor): FlattenExtractor(
      (flatten): Flatten(start_dim=1, end_dim=-1)
    )
    (qf0): Sequential(
      (0): Linear(in_features=204, out_features=256, bias=True)
      (1): ReLU()
      (2): Linear(in_features=256, out_features=256, bias=True)
      (3): ReLU()
      (4): Linear(in_features=256, out_features=1, bias=True)
    )
    (qf1): Sequential(
      (0): Linear(in_features=204, out_features=256, bias=True)
      (1): ReLU()
      (2): Linear(in_features=256, out_features=2

Let's see agent's learning process

In [62]:
learning_process = pd.read_csv("resultadosTFG/set_3/sac/progress.csv")
learning_process

time/time_elapsed  train/n_updates  train/learning_rate  train/critic_loss  \
0                151            11727               0.0001          97.338196   
1                318            23555               0.0001         124.782188   
2                483            35383               0.0001          15.850610   
3                651            47211               0.0001           6.360431   

   time/fps  train/actor_loss  time/total_timesteps  train/ent_coef_loss  \
0        78       1230.866699                 11828           -15.590743   
1        74        520.109375                 23656          -102.088470   
2        73        228.023743                 35484           -92.091583   
3        72        111.796936                 47312           -73.770493   

   time/episodes  train/ent_coef  train/reward  
0              4        0.239251     -6.316020  
1              8        0.073493     -6.911640  
2             12        0.023516     -8.053040  
3             16        0.007580     -7.540032

Agent's training results

In [63]:
def plot_metrics(df, n_rows, n_cols):
    fig, axes = plt.subplots(nrows=n_rows, ncols=n_cols, figsize=(5 * n_cols, 5 * n_rows))
    axes = axes.flatten()  # Flatten the array of axes if more than one row or column

    metrics = [
        ('train/reward', 'Reward'),
        ('train/actor_loss', 'Actor Loss'),
        ('train/ent_coef_loss', 'Entropy coefficient Loss'),
        ('train/ent_coef', 'Entropy coefficient'),
        ('train/critic_loss', 'Critic Loss')
    ]

    # Plot each metric
    for ax, (metric, title) in zip(axes, metrics):
        ax.plot(df['time/total_timesteps'], df[metric], label=title)
        ax.set_xlabel('Total Timesteps')
        ax.set_ylabel(title)
        ax.set_title(title)
        ax.grid(True)
        ax.legend()

    plt.tight_layout()
    plt.savefig(f'resultadosTFG/set_3/sac/trainingStatsResults.png')
    plt.close()

df = learning_process
plot_metrics(df, n_rows=5, n_cols=1)  # Modify n_rows and n_cols as needed

# Testing

There is a new environment for testing

We feed the environment with the testing dataset we prepared before (from start test date to end test date: with closing prices, etc)

In [64]:
e_trade_gym = StockTradingEnv(df = trade, turbulence_threshold = 70,risk_indicator_col='vix', **env_kwargs)
e_trade_gym

Environment from Stable baselines3; observations is a matrix containing the inputs {balance, close price, shares, N-technical indicators}

In [65]:
env_trade, obs_trade = e_trade_gym.get_sb_env()
env_trade

In [66]:
obs_trade

array([[1.00000000e+06, 1.40653503e+02, 1.95822250e+02, 1.67727432e+02,
        2.26000000e+02, 1.83513977e+02, 2.74900909e+02, 5.07116699e+01,
        9.38071136e+01, 1.75438217e+02, 3.52330719e+02, 3.07771088e+02,
        2.03622498e+02, 1.20424370e+02, 5.01258202e+01, 1.48433228e+02,
        1.54524475e+02, 4.87658424e+01, 2.28277771e+02, 1.26340294e+02,
        7.50690994e+01, 2.82857391e+02, 1.42315765e+02, 1.30338409e+02,
        1.43675766e+02, 3.77384949e+02, 2.25689667e+02, 4.58676872e+01,
        4.03038139e+01, 4.38215218e+01, 0.00000000e+00, 0.00000000e+00,
        0.00000000e+00, 0.00000000e+00, 0.00000000e+00, 0.00000000e+00,
        0.00000000e+00, 0.00000000e+00, 0.00000000e+00, 0.00000000e+00,
        0.00000000e+00, 0.00000000e+00, 0.00000000e+00, 0.00000000e+00,
        0.00000000e+00, 0.00000000e+00, 0.00000000e+00, 0.00000000e+00,
        0.00000000e+00, 0.00000000e+00, 0.00000000e+00, 0.00000000e+00,
        0.00000000e+00, 0.00000000e+00, 0.00000000e+00, 0.000000

In [67]:
trade

date   tic        open        high         low       close  \
0    2021-10-01  AAPL  141.899994  142.919998  139.110001  140.653503   
0    2021-10-01  AMGN  213.589996  214.610001  210.800003  195.822250   
0    2021-10-01   AXP  168.500000  175.119995  168.479996  167.727432   
0    2021-10-01    BA  222.850006  226.720001  220.600006  226.000000   
0    2021-10-01   CAT  192.899994  195.869995  191.240005  183.513977   
..          ...   ...         ...         ...         ...         ...   
352  2023-02-27   UNH  488.769989  490.940002  481.959991  472.278229   
352  2023-02-27     V  220.729996  221.440002  219.339996  218.230591   
352  2023-02-27    VZ   38.990002   39.150002   38.630001   35.602482   
352  2023-02-27   WBA   36.049999   36.080002   35.270000   32.621925   
352  2023-02-27   WMT   47.570000   47.696667   46.886665   46.121086   

         volume  day  supertrend  high_5_sma        tema        chop  \
0    94639600.0  4.0  151.962212  144.492001  140.060804   52.599639   
0     2629400.0  4.0  178.648656  215.557999  195.572014  129.938977   
0     3956000.0  4.0  152.435852  175.300000  165.806740   67.869157   
0     9113600.0  4.0  209.674360  227.198001  224.813103   49.304866   
0     3695500.0  4.0  227.936156  199.956000  183.268493   83.959205   
..          ...  ...         ...         ...         ...         ...   
352   3006200.0  0.0  528.902604  494.414001  472.307649   73.038919   
352   4255300.0  0.0  215.501733  221.592001  217.546533   46.661686   
352  14210900.0  0.0   48.206669   39.360000   35.438624  104.818863   
352   5580100.0  0.0   42.533680   36.282000   32.709818  121.678302   
352  16647300.0  0.0   50.711280   48.407333   46.078058   70.251888   

           vix  turbulence  
0    21.100000  120.031019  
0    21.100000  120.031019  
0    21.100000  120.031019  
0    21.100000  120.031019  
0    21.100000  120.031019  
..         ...         ...  
352  20.950001    7.163951  
352  20.950001    7.163951  
352  20.950001    7.163951  
352  20.950001    7.163951  
352  20.950001    7.163951  

[10237 rows x 14 columns]

## A2C

Test, predict

In [68]:
trained_model = trained_a2c
df_account_value_a2c, df_actions_a2c = DRLAgent.DRL_prediction(
    model=trained_model, 
    environment = e_trade_gym)

el modelo es 
estos son los test obs
[[1.00000000e+06 1.40653503e+02 1.95822250e+02 1.67727432e+02
  2.26000000e+02 1.83513977e+02 2.74900909e+02 5.07116699e+01
  9.38071136e+01 1.75438217e+02 3.52330719e+02 3.07771088e+02
  2.03622498e+02 1.20424370e+02 5.01258202e+01 1.48433228e+02
  1.54524475e+02 4.87658424e+01 2.28277771e+02 1.26340294e+02
  7.50690994e+01 2.82857391e+02 1.42315765e+02 1.30338409e+02
  1.43675766e+02 3.77384949e+02 2.25689667e+02 4.58676872e+01
  4.03038139e+01 4.38215218e+01 0.00000000e+00 0.00000000e+00
  0.00000000e+00 0.00000000e+00 0.00000000e+00 0.00000000e+00
  0.00000000e+00 0.00000000e+00 0.00000000e+00 0.00000000e+00
  0.00000000e+00 0.00000000e+00 0.00000000e+00 0.00000000e+00
  0.00000000e+00 0.00000000e+00 0.00000000e+00 0.00000000e+00
  0.00000000e+00 0.00000000e+00 0.00000000e+00 0.00000000e+00
  0.00000000e+00 0.00000000e+00 0.00000000e+00 0.00000000e+00
  0.00000000e+00 0.00000000e+00 0.00000000e+00 1.51962219e+02
  1.78648651e+02 1.52435852e+02 2

 las observaciones devueltas en el for son  [[1.87869266e-01 1.56728943e+02 2.11290344e+02 1.64360504e+02
  1.78389999e+02 2.02082367e+02 1.99888885e+02 5.09546204e+01
  1.56997192e+02 1.33205872e+02 3.09305359e+02 2.99673767e+02
  1.75792572e+02 1.12083603e+02 4.40600891e+01 1.58975815e+02
  1.23384506e+02 5.36487236e+01 2.10933563e+02 1.05128563e+02
  7.25135651e+01 2.80513184e+02 1.22462227e+02 1.36917847e+02
  1.63817703e+02 4.74140503e+02 1.94529404e+02 4.60459976e+01
  4.22190857e+01 4.57893448e+01 9.68000000e+02 0.00000000e+00
  0.00000000e+00 0.00000000e+00 5.78000000e+02 0.00000000e+00
  0.00000000e+00 4.66000000e+02 0.00000000e+00 2.50000000e+01
  0.00000000e+00 0.00000000e+00 0.00000000e+00 5.40000000e+02
  0.00000000e+00 1.79000000e+02 1.97500000e+03 0.00000000e+00
  0.00000000e+00 0.00000000e+00 5.29000000e+02 5.51000000e+02
  1.00000000e+00 2.19900000e+03 0.00000000e+00 0.00000000e+00
  0.00000000e+00 0.00000000e+00 1.27000000e+02 1.73055161e+02
  1.78648651e+02 1.8938501

Plot and Save testing results, Portfolio Value

In [69]:
df_account_value_a2c['date'] = pd.to_datetime(df_account_value_a2c['date']).dt.normalize()
plt.figure(figsize=(14, 7))
plt.plot(df_account_value_a2c['date'], df_account_value_a2c['account_value'])

# Setting major locator
locator = mdates.MonthLocator(interval=1)  # Show a tick every week
plt.gca().xaxis.set_major_locator(locator)

# Setting formatter
formatter = mdates.DateFormatter('%Y-%m-%d')
plt.gca().xaxis.set_major_formatter(formatter)

# Optionally, auto-format date labels to prevent overlap
plt.gcf().autofmt_xdate()

plt.title('Account Value Testing for A2C')
plt.xlabel('Date')
plt.ylabel('Account Value')
plt.grid(True)

plt.savefig(f'resultadosTFG/set_3/a2c/testing/accountValue.png')
plt.close()

Trades made in testing

In [70]:
display(df_actions_a2c)

AAPL  AMGN  AXP  BA  CAT  CRM  CSCO  CVX  DIS  GS  ...  MRK  MSFT  \
date                                                           ...              
2021-10-01   100     0   16  58    0    0     0  100  100   0  ...    0   100   
2021-10-04   100     0   16  58    0    0     0  100  100   0  ...    0   100   
2021-10-05   100     0   16  58    0    0     0  100  100   0  ...    0   100   
2021-10-06   100     0   16  58    0    0     0  100  100   0  ...    0   100   
2021-10-07   100     0   16  58    0    0     0  100  100   0  ...    0   100   
...          ...   ...  ...  ..  ...  ...   ...  ...  ...  ..  ...  ...   ...   
2023-02-17     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-02-21     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-02-22     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-02-23     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-02-24     0     0    0   0    0    0     0    0    0   0  ...    0     0   

            NKE  PG  TRV  UNH   V  VZ  WBA  WMT  
date                                             
2021-10-01    0   0  100   85  83  27  100    0  
2021-10-04    0   0  100   85  83  27  100    0  
2021-10-05    0   0  100   85  83  27  100    0  
2021-10-06    0   0  100   85  83  27  100    0  
2021-10-07    0   0  100   85  83  27  100    0  
...         ...  ..  ...  ...  ..  ..  ...  ...  
2023-02-17    0   0    0    0   0   0    0    0  
2023-02-21    0   0    0    0   0   0    0    0  
2023-02-22    0   0    0    0   0   0    0    0  
2023-02-23    0   0    0    0   0   0    0    0  
2023-02-24    0   0    0    0   0   0    0    0  

[352 rows x 29 columns]

## PPO

Test, predict

In [71]:
trained_model = trained_ppo
df_account_value_ppo, df_actions_ppo = DRLAgent.DRL_prediction(
    model=trained_model, 
    environment = e_trade_gym)

el modelo es 
estos son los test obs
[[1.00000000e+06 1.40653503e+02 1.95822250e+02 1.67727432e+02
  2.26000000e+02 1.83513977e+02 2.74900909e+02 5.07116699e+01
  9.38071136e+01 1.75438217e+02 3.52330719e+02 3.07771088e+02
  2.03622498e+02 1.20424370e+02 5.01258202e+01 1.48433228e+02
  1.54524475e+02 4.87658424e+01 2.28277771e+02 1.26340294e+02
  7.50690994e+01 2.82857391e+02 1.42315765e+02 1.30338409e+02
  1.43675766e+02 3.77384949e+02 2.25689667e+02 4.58676872e+01
  4.03038139e+01 4.38215218e+01 0.00000000e+00 0.00000000e+00
  0.00000000e+00 0.00000000e+00 0.00000000e+00 0.00000000e+00
  0.00000000e+00 0.00000000e+00 0.00000000e+00 0.00000000e+00
  0.00000000e+00 0.00000000e+00 0.00000000e+00 0.00000000e+00
  0.00000000e+00 0.00000000e+00 0.00000000e+00 0.00000000e+00
  0.00000000e+00 0.00000000e+00 0.00000000e+00 0.00000000e+00
  0.00000000e+00 0.00000000e+00 0.00000000e+00 0.00000000e+00
  0.00000000e+00 0.00000000e+00 0.00000000e+00 1.51962219e+02
  1.78648651e+02 1.52435852e+02 2

Save Plot of Portfolio Value

In [72]:
df_account_value_ppo['date'] = pd.to_datetime(df_account_value_ppo['date']).dt.normalize()
plt.figure(figsize=(14, 7))
plt.plot(df_account_value_ppo['date'], df_account_value_ppo['account_value'])

# Setting major locator
locator = mdates.MonthLocator(interval=1)  # Show a tick every week
plt.gca().xaxis.set_major_locator(locator)

# Setting formatter
formatter = mdates.DateFormatter('%Y-%m-%d')
plt.gca().xaxis.set_major_formatter(formatter)

# Optionally, auto-format date labels to prevent overlap
plt.gcf().autofmt_xdate()

plt.title('Account Value Testing for PPO')
plt.xlabel('Date')
plt.ylabel('Account Value')
plt.grid(True)

plt.savefig(f'resultadosTFG/set_3/ppo/testing/accountValue.png')
plt.close()


Trades made in testing

In [73]:
df_actions_ppo.tail(40)

AAPL  AMGN  AXP  BA  CAT  CRM  CSCO  CVX  DIS  GS  ...  MRK  MSFT  \
date                                                           ...              
2022-12-28     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2022-12-29     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2022-12-30     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-01-03     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-01-04     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-01-05     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-01-06     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-01-09     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-01-10     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-01-11     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-01-12     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-01-13     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-01-17     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-01-18     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-01-19     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-01-20     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-01-23     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-01-24     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-01-25     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-01-26     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-01-27     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-01-30     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-01-31     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-02-01     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-02-02     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-02-03     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-02-06     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-02-07     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-02-08     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-02-09     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-02-10     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-02-13     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-02-14     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-02-15     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-02-16     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-02-17     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-02-21     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-02-22     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-02-23     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-02-24     0     0    0   0    0    0     0    0    0   0  ...    0     0   

            NKE  PG  TRV  UNH  V  VZ  WBA  WMT  
date                                            
2022-12-28    0   0    0    0  0   0    0    0  
2022-12-29    0   0    0    0  0   0    0    0  
2022-12-30    0   0    0    0  0   0    0    0  
2023-01-03    0   0    0    0  0   0    0    0  
2023-01-04    0   0    0    0  0   0    0    0  
2023-01-05    0   0    0    0  0   0    0    0  
2023-01-06    0   0    0    0  0   0    0    0  
2023-01-09    0   0    0    0  0   0    0    0  
2023-01-10    0   0    0    0  0   0    0    0  
2023-01-11    0   0    0    0  0   0    0    0  
2023-01-12    0   0  

## DDPG

Test DDPG, predict

In [74]:
trained_model = trained_ddpg
df_account_value_ddpg, df_actions_ddpg = DRLAgent.DRL_prediction(
    model=trained_model, 
    environment = e_trade_gym)

el modelo es 
estos son los test obs
[[1.00000000e+06 1.40653503e+02 1.95822250e+02 1.67727432e+02
  2.26000000e+02 1.83513977e+02 2.74900909e+02 5.07116699e+01
  9.38071136e+01 1.75438217e+02 3.52330719e+02 3.07771088e+02
  2.03622498e+02 1.20424370e+02 5.01258202e+01 1.48433228e+02
  1.54524475e+02 4.87658424e+01 2.28277771e+02 1.26340294e+02
  7.50690994e+01 2.82857391e+02 1.42315765e+02 1.30338409e+02
  1.43675766e+02 3.77384949e+02 2.25689667e+02 4.58676872e+01
  4.03038139e+01 4.38215218e+01 0.00000000e+00 0.00000000e+00
  0.00000000e+00 0.00000000e+00 0.00000000e+00 0.00000000e+00
  0.00000000e+00 0.00000000e+00 0.00000000e+00 0.00000000e+00
  0.00000000e+00 0.00000000e+00 0.00000000e+00 0.00000000e+00
  0.00000000e+00 0.00000000e+00 0.00000000e+00 0.00000000e+00
  0.00000000e+00 0.00000000e+00 0.00000000e+00 0.00000000e+00
  0.00000000e+00 0.00000000e+00 0.00000000e+00 0.00000000e+00
  0.00000000e+00 0.00000000e+00 0.00000000e+00 1.51962219e+02
  1.78648651e+02 1.52435852e+02 2

Store graph of the value of portfolio

In [75]:
df_account_value_ddpg['date'] = pd.to_datetime(df_account_value_ddpg['date']).dt.normalize()
plt.figure(figsize=(14, 7))
plt.plot(df_account_value_ddpg['date'], df_account_value_ddpg['account_value'])

# Setting major locator
locator = mdates.MonthLocator(interval=1)  # Show a tick every week
plt.gca().xaxis.set_major_locator(locator)

# Setting formatter
formatter = mdates.DateFormatter('%Y-%m-%d')
plt.gca().xaxis.set_major_formatter(formatter)

# Optionally, auto-format date labels to prevent overlap
plt.gcf().autofmt_xdate()

plt.title('Account Value Testing for DDPG')
plt.xlabel('Date')
plt.ylabel('Account Value')
plt.grid(True)

plt.savefig(f'resultadosTFG/set_3/ddpg/testing/accountValue.png')
plt.close()


Trades made in testing

In [76]:
df_actions_ddpg.head(30)

AAPL  AMGN  AXP   BA  CAT  CRM  CSCO  CVX  DIS   GS  ...  MRK  \
date                                                             ...        
2021-10-01   100   100    0  100  100    0     0  100    0  100  ...  100   
2021-10-04   100   100    0  100  100    0     0  100    0  100  ...  100   
2021-10-05   100   100    0  100  100    0     0  100    0  100  ...  100   
2021-10-06   100   100    0  100  100    0     0  100    0  100  ...  100   
2021-10-07     0   100    0  100  100    0     0  100    0   45  ...    0   
2021-10-08     0     0    0    0    0    0     0    0    0    0  ...    0   
2021-10-11     0     0    0    0    0    0     0    0    0    0  ...    0   
2021-10-12     0     0    0    0    0    0     0    0    0    0  ...    0   
2021-10-13     0     0    0    0    0    0     0    0    0    0  ...    0   
2021-10-14     0     0    0    0    0    0     0    0    0    0  ...    0   
2021-10-15     0     0    0    0    0    0     0    0    0    0  ...    0   
2021-10-18     0     0    0    0    0    0     0    0    0    0  ...    0   
2021-10-19     0     0    0    0    0    0     0    0    0    0  ...    0   
2021-10-20     0     0    0    0    0    0     0    0    0    0  ...    0   
2021-10-21     0     0    0    0    0    0     0    0    0    0  ...    0   
2021-10-22     0     0    0    0    0    0     0    0    0    0  ...    0   
2021-10-25     0     0    0    0    0    0     0    0    0    0  ...    0   
2021-10-26     0     0    0    0    0    0     0    0    0    0  ...    0   
2021-10-27     0     0    0    0    0    0     0    0    0    0  ...    0   
2021-10-28     0     0    0    0    0    0     0    0    0    0  ...    0   
2021-10-29     0     0    0    0    0    0     0    0    0    0  ...    0   
2021-11-01     0     0    0    0    0    0     0    0    0    0  ...    0   
2021-11-02     0     0    0    0    0    0     0    0    0    0  ...    0   
2021-11-03     0     0    0    0    0    0     0    0    0    0  ...    0   
2021-11-04     0     0    0    0    0    0     0    0    0    0  ...    0   
2021-11-05     0     0    0    0    0    0     0    0    0    0  ...    0   
2021-11-08     0     0    0    0    0    0     0    0    0    0  ...    0   
2021-11-09     0     0    0    0    0    0     0    0    0    0  ...    0   
2021-11-10     0     0    0    0    0    0     0    0    0    0  ...    0   
2021-11-11     0     0    0    0    0    0     0    0    0    0  ...    0   

            MSFT  NKE   PG  TRV  UNH    V   VZ  WBA  WMT  
date                                                      
2021-10-01     0    0  100    0    0  100  100  100    0  
2021-10-04     0    0  100    0    0  100  100  100    0  
2021-10-05     0    0  100    0    0  100  100  100    0  
2021-10-06     0    0  100    0    0  100  100  100    0  
2021-10-07     0    0    0    0    0    0    0    0    0  
2021-10-08     0    0    0    0    0    0    0    1    0  
2021-10-11     0    0    0    0    0    0    0    0    0  
2021-10-12     0    0    0    0    0    0    0    0    0  
2021-10-13     0    0    0    0    0    0    0    0    0  
2021-10-14     0    0    0    0    0    0    0    0    0  
2021-10-15     0    0    0    0    0    0    0    0    0  
2021-10-18     0    0    0    0    0    0    0    0    0  
2021-10-19     0    0    0    0    0    0    0    0    0  
2021-10-20     0    0    0    0    0    0    0    0    0  
2021-10-21     0    0    0    0    0    0    0    0    0  
2021-10-22     0    0    0    0    0    0    0    0    0  
2021-10-25     0    0    0    0    0    0    0    0    0  
2021-10-26     0    0    0    0    0    0    0    0    0  
2021-10-27     0    0    0    0    0    0    0    0    0  
2021-10-28     0    0    0    0    0    0    0    0    0  
2021-10-29     0    0    0    0    0    0    0    0    0  
2021-11-01     0    0    0    0    0    0    0    0    0  
2021-11-02     0    0    0    0    0    0    0    0    0  
2021-11-03     0    0    0    0    0    0    0    0    0  
2021-11-04   

## TD3

Test TD3, predict

In [77]:
trained_model = trained_td3
df_account_value_td3, df_actions_td3 = DRLAgent.DRL_prediction(
    model=trained_model, 
    environment = e_trade_gym)

el modelo es 
estos son los test obs
[[1.00000000e+06 1.40653503e+02 1.95822250e+02 1.67727432e+02
  2.26000000e+02 1.83513977e+02 2.74900909e+02 5.07116699e+01
  9.38071136e+01 1.75438217e+02 3.52330719e+02 3.07771088e+02
  2.03622498e+02 1.20424370e+02 5.01258202e+01 1.48433228e+02
  1.54524475e+02 4.87658424e+01 2.28277771e+02 1.26340294e+02
  7.50690994e+01 2.82857391e+02 1.42315765e+02 1.30338409e+02
  1.43675766e+02 3.77384949e+02 2.25689667e+02 4.58676872e+01
  4.03038139e+01 4.38215218e+01 0.00000000e+00 0.00000000e+00
  0.00000000e+00 0.00000000e+00 0.00000000e+00 0.00000000e+00
  0.00000000e+00 0.00000000e+00 0.00000000e+00 0.00000000e+00
  0.00000000e+00 0.00000000e+00 0.00000000e+00 0.00000000e+00
  0.00000000e+00 0.00000000e+00 0.00000000e+00 0.00000000e+00
  0.00000000e+00 0.00000000e+00 0.00000000e+00 0.00000000e+00
  0.00000000e+00 0.00000000e+00 0.00000000e+00 0.00000000e+00
  0.00000000e+00 0.00000000e+00 0.00000000e+00 1.51962219e+02
  1.78648651e+02 1.52435852e+02 2

Store graph of the value of portfolio

In [78]:
df_account_value_td3['date'] = pd.to_datetime(df_account_value_td3['date']).dt.normalize()
plt.figure(figsize=(14, 7))
plt.plot(df_account_value_td3['date'], df_account_value_td3['account_value'])

# Setting major locator
locator = mdates.MonthLocator(interval=1)  # Show a tick every week
plt.gca().xaxis.set_major_locator(locator)

# Setting formatter
formatter = mdates.DateFormatter('%Y-%m-%d')
plt.gca().xaxis.set_major_formatter(formatter)

# Optionally, auto-format date labels to prevent overlap
plt.gcf().autofmt_xdate()

plt.title('Account Value Testing for TD3')
plt.xlabel('Date')
plt.ylabel('Account Value')
plt.grid(True)

plt.savefig(f'resultadosTFG/set_3/td3/testing/accountValue.png')
plt.close()


Trades made in testing

In [79]:
df_actions_td3.head(30)

AAPL  AMGN  AXP  BA  CAT  CRM  CSCO  CVX  DIS   GS  ...  MRK  \
date                                                            ...        
2021-10-01     0     0    0   0  100    0   100  100    0  100  ...  100   
2021-10-04     0     0    0   0  100    0   100  100    0  100  ...  100   
2021-10-05     0     0    0   0  100    0   100  100    0  100  ...  100   
2021-10-06     0     0    0   0  100    0   100  100    0  100  ...  100   
2021-10-07     0     0    0   0 -100    0     0   96    0    0  ...    0   
2021-10-08     0     0    0   0 -100    0     0   92    0    0  ...    0   
2021-10-11     0     0    0   0 -100    0     0   90    0    0  ...    0   
2021-10-12     0     0    0   0 -100    0     0   87    0    0  ...    0   
2021-10-13     0     0    0   0    0    0     0    0    0    0  ...    0   
2021-10-14     0     0    0   0    0    0     0    0    0    0  ...    0   
2021-10-15     0     0    0   0    0    0     0    0    0    0  ...    0   
2021-10-18     0     0    0   0    0    0     0    0    0    0  ...    0   
2021-10-19     0     0    0   0    0    0     0    0    0    0  ...    0   
2021-10-20     0     0    0   0    0    0     0    0    0    0  ...    0   
2021-10-21     0     0    0   0    0    0     0    0    0    0  ...    0   
2021-10-22     0     0    0   0    0    0     0    0    0    0  ...    0   
2021-10-25     0     0    0   0    0    0     0    0    0    0  ...    0   
2021-10-26     0     0    0   0    0    0     0    0    0    0  ...    0   
2021-10-27     0     0    0   0    0    0     0    0    0    0  ...    0   
2021-10-28     0     0    0   0    0    0     0    0    0    0  ...    0   
2021-10-29     0     0    0   0    0    0     0    0    0    0  ...    0   
2021-11-01     0     0    0   0    0    0     0    0    0    0  ...    0   
2021-11-02     0     0    0   0    0    0     0    0    0    0  ...    0   
2021-11-03     0     0    0   0    0    0     0    0    0    0  ...    0   
2021-11-04     0     0    0   0    0    0     0    0    0    0  ...    0   
2021-11-05     0     0    0   0    0    0     0    0    0    0  ...    0   
2021-11-08     0     0    0   0    0    0     0    0    0    0  ...    0   
2021-11-09     0     0    0   0    0    0     0    0    0    0  ...    0   
2021-11-10     0     0    0   0    0    0     0    0    0    0  ...    0   
2021-11-11     0     0    0   0    0    0     0    0    0    0  ...    0   

            MSFT  NKE   PG  TRV  UNH    V  VZ  WBA  WMT  
date                                                     
2021-10-01   100    0  100  100  100  100   0  100  100  
2021-10-04   100    0  100  100  100  100   0  100  100  
2021-10-05   100    0  100  100  100  100   0  100  100  
2021-10-06   100    0  100  100   76    1   0  100  100  
2021-10-07     0    0    0    0    0    0   0    0  100  
2021-10-08     0    0    0    0    0    0   0    0  100  
2021-10-11     0    0    0    0    0    0   0    0  100  
2021-10-12     0    0    0    0    0    0   0    1  100  
2021-10-13     0    0    0    0    0    0   0    0    0  
2021-10-14     0    0    0    0    0    0   0    0    0  
2021-10-15     0    0    0    0    0    0   0    0    0  
2021-10-18     0    0    0    0    0    0   0    0    0  
2021-10-19     0    0    0    0    0    0   0    0    0  
2021-10-20     0    0    0    0    0    0   0    0    0  
2021-10-21     0    0    0    0    0    0   0    0    0  
2021-10-22     0    0    0    0    0    0   0    0    0  
2021-10-25     0    0    0    0    0    0   0    0    0  
2021-10-26     0    0    0    0    0    0   0    0    0  
2021-10-27     0    0    0    0    0    0   0    0    0  
2021-10-28     0    0    0    0    0    0   0    0    0  
2021-10-29     0    0    0    0    0    0   0    0    0  
2021-11-01     0    0    0    0    0    0   0    0    0  
2021-11-02     0    0    0    0    0    0   0    0    0  
2021-11-03     0    0    0    0    0    0   0    0    0  
2021-11-04     0    0    0    0    0    0   0    0    0  
2021-11-05   

## SAC

Test SAC, predict

Account value is the DF that stores the history of the value of the assets (portfolio value)

In [80]:
trained_model = trained_sac
df_account_value_sac, df_actions_sac = DRLAgent.DRL_prediction(
    model=trained_model, 
    environment = e_trade_gym)

el modelo es 
estos son los test obs
[[1.00000000e+06 1.40653503e+02 1.95822250e+02 1.67727432e+02
  2.26000000e+02 1.83513977e+02 2.74900909e+02 5.07116699e+01
  9.38071136e+01 1.75438217e+02 3.52330719e+02 3.07771088e+02
  2.03622498e+02 1.20424370e+02 5.01258202e+01 1.48433228e+02
  1.54524475e+02 4.87658424e+01 2.28277771e+02 1.26340294e+02
  7.50690994e+01 2.82857391e+02 1.42315765e+02 1.30338409e+02
  1.43675766e+02 3.77384949e+02 2.25689667e+02 4.58676872e+01
  4.03038139e+01 4.38215218e+01 0.00000000e+00 0.00000000e+00
  0.00000000e+00 0.00000000e+00 0.00000000e+00 0.00000000e+00
  0.00000000e+00 0.00000000e+00 0.00000000e+00 0.00000000e+00
  0.00000000e+00 0.00000000e+00 0.00000000e+00 0.00000000e+00
  0.00000000e+00 0.00000000e+00 0.00000000e+00 0.00000000e+00
  0.00000000e+00 0.00000000e+00 0.00000000e+00 0.00000000e+00
  0.00000000e+00 0.00000000e+00 0.00000000e+00 0.00000000e+00
  0.00000000e+00 0.00000000e+00 0.00000000e+00 1.51962219e+02
  1.78648651e+02 1.52435852e+02 2

Store graph of the value of portfolio

In [81]:
df_account_value_sac['date'] = pd.to_datetime(df_account_value_sac['date']).dt.normalize()
plt.figure(figsize=(14, 7))
plt.plot(df_account_value_sac['date'], df_account_value_sac['account_value'])

# Setting major locator
locator = mdates.MonthLocator(interval=1)  # Show a tick every week
plt.gca().xaxis.set_major_locator(locator)

# Setting formatter
formatter = mdates.DateFormatter('%Y-%m-%d')
plt.gca().xaxis.set_major_formatter(formatter)

# Optionally, auto-format date labels to prevent overlap
plt.gcf().autofmt_xdate()

plt.title('Account Value Testing for SAC')
plt.xlabel('Date')
plt.ylabel('Account Value')
plt.grid(True)

plt.savefig(f'resultadosTFG/set_3/sac/testing/accountValue.png')
plt.close()


Trades made in testing

In [82]:
df_actions_sac.head(30)

AAPL  AMGN  AXP  BA  CAT  CRM  CSCO  CVX  DIS  GS  ...  MRK  MSFT  \
date                                                           ...              
2021-10-01     0    96   95   0    0    0    51   87   81  94  ...    0     0   
2021-10-04     0    96   95   0    0    0    51   87   81  94  ...    0     0   
2021-10-05     0    96   95   0    0    0    51   87   81  94  ...    0     0   
2021-10-06     0    96   95   0    0    0    51   87   81  94  ...    0     0   
2021-10-07     0    96   95   0    0    0    51   87   81  94  ...    0     0   
2021-10-08     0    96    0   0    0    0     0    0    0   0  ...    0     0   
2021-10-11     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2021-10-12     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2021-10-13     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2021-10-14     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2021-10-15     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2021-10-18     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2021-10-19     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2021-10-20     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2021-10-21     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2021-10-22     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2021-10-25     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2021-10-26     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2021-10-27     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2021-10-28     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2021-10-29     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2021-11-01     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2021-11-02     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2021-11-03     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2021-11-04     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2021-11-05     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2021-11-08     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2021-11-09     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2021-11-10     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2021-11-11     0     0    0   0    0    0     0    0    0   0  ...    0     0   

            NKE  PG  TRV  UNH   V  VZ  WBA  WMT  
date                                             
2021-10-01   50  87    0    0  92  33    0    0  
2021-10-04   50  87    0    0  92  33    0    0  
2021-10-05   50  87    0    0  92  33    0    0  
2021-10-06   50  87    0    0  92  33    0    0  
2021-10-07   50  87    0    0  92  33    0    0  
2021-10-08    0   1    0    0   0   0    0    0  
2021-10-11    0   0    0    0   0   0    0    0  
2021-10-12    0   0    0    0   0   0    0    0  
2021-10-13    0   0    0    0   0   0    0    0  
2021-10-14    0   0    0    0   0   0    0    0  
2021-10-15    0   0    0    0   0   0    0    0  
2021-10-18    0   0    0    0   0   0    0    0  
2021-10-19    0   0    0    0   0   0    0    0  
2021-10-20    0   0    0    0   0   0    0    0  
2021-10-21    0   0    0    0   0   0    0    0  
2021-10-22    0   0    0    0   0   0    0    0  
2021-10-25    0   0    0    0   0   0    0    0  
2021-10-26    0   0    0    0   0   0    0    0  
2021-10-27    0   0    0    0   0   0    0    0  
2021-10-28    0   0    0    0   0   0    0    0  
2021-10-29    0   0    0    0   0   0    0    0  
2021-11-01    0   0    0    0   0   0    0    0  
2021-11-02    0   0    0    0   0   0    0    0  
2021-11-03    0   0    0    0   0   0    0    0  
2021-11-04    0   0    0    0   0   0    0    0  
2021-11-05    0   0    0    0   0   0    0    0  
2021-11-08    0   0

Obtain results to then merge: merge in one DF the Portfolio Value given by each algorithm

In [83]:
df_result_a2c = df_account_value_a2c.set_index(df_account_value_a2c.columns[0])
df_result_a2c.rename(columns = {'account_value':'a2c'}, inplace = True)
df_result_ddpg = df_account_value_ddpg.set_index(df_account_value_ddpg.columns[0])
df_result_ddpg.rename(columns = {'account_value':'ddpg'}, inplace = True)
df_result_td3 = df_account_value_td3.set_index(df_account_value_td3.columns[0])
df_result_td3.rename(columns = {'account_value':'td3'}, inplace = True)
df_result_ppo = df_account_value_ppo.set_index(df_account_value_ppo.columns[0])
df_result_ppo.rename(columns = {'account_value':'ppo'}, inplace = True)
df_result_sac = df_account_value_sac.set_index(df_account_value_sac.columns[0])
df_result_sac.rename(columns = {'account_value':'sac'}, inplace = True)

We can also get stats from each stock individually (even though the analysis won't focus on that)

In [84]:
#baseline stats

print("==============Get Baseline Stats===========")
print("==============Baseline Stats of Profitability from DJIA===========")
print("This is the real performance of the index")
df_dji_ = get_baseline(
        ticker="^DJI", 
        start = TEST_START_DATE,
        end = TEST_END_DATE)
stats = backtest_stats(df_dji_, value_col_name = 'close')

==============Get Baseline Stats===========
==============Baseline Stats of Profitability from DJIA===========
This is the real performance of the index


[*********************100%%**********************]  1 of 1 completed

Shape of DataFrame:  (354, 8)
Annual return         -0.034876
Cumulative returns    -0.048644
Annual volatility      0.181612
Sharpe ratio          -0.105351
Calmar ratio          -0.158953
Stability              0.280983
Max drawdown          -0.219408
Omega ratio            0.982546
Sortino ratio         -0.146974
Skew                        NaN
Kurtosis                    NaN
Tail ratio             0.970602
Daily value at risk   -0.022957
dtype: float64


get_baseline vuelve a fetchear los stocks de YahooFinance dadas esas fechas.

backtest_stats llama a get daily return y luego saca stats de esa Serie con metodo que pide:

    """
    Calculates various performance metrics of a strategy, for use in
    plotting.show_perf_stats.

    Parameters
    ----------
    returns : pd.Series
        Daily returns of the strategy, noncumulative.
         - See full explanation in tears.create_full_tear_sheet.
    factor_returns : pd.Series, optional
        Daily noncumulative returns of the benchmark factor to which betas are
        computed. Usually a benchmark such as market returns.
         - This is in the same style as returns.
         - If None, do not compute alpha, beta, and information ratio.
    positions : pd.DataFrame
        Daily net position values.
         - See full explanation in tears.create_full_tear_sheet.
    transactions : pd.DataFrame
        Prices and amounts of executed trades. One row per trade.
        - See full explanation in tears.create_full_tear_sheet.
    turnover_denom : str
        Either AGB or portfolio_value, default AGB.
        - See full explanation in txn.get_turnover.

    Returns
    -------
    pd.Series
        Performance metrics.
    """

get daily profitability * invested amount = portfolio value in case of investing 1000000$ on DJ and not touching it

In [85]:
df_dji = pd.DataFrame()
df_dji['date'] = df_account_value_a2c['date']
df_dji['account_value'] = df_dji_['close'] / df_dji_['close'][0] * env_kwargs["initial_amount"] # get daily profitability * invested amount = portfolio value in case of investing 1000000$ on DJ and not touching it
#df_dji.to_csv("df_dji.csv")
df_dji = df_dji.set_index(df_dji.columns[0])
#df_dji.to_csv("df_dji+.csv")

In [86]:
df_dji.rename(columns = {'account_value':'dji'}, inplace = True)

In [87]:
df_result_td3

td3
date                    
2021-10-01  1.000000e+06
2021-10-04  9.972112e+05
2021-10-05  1.002644e+06
2021-10-06  1.005675e+06
2021-10-07  1.017347e+06
...                  ...
2023-02-21  1.072328e+06
2023-02-22  1.067711e+06
2023-02-23  1.072953e+06
2023-02-24  1.066027e+06
2023-02-27  1.066999e+06

[353 rows x 1 columns]

Compare DJIA with the rest of the algorithms

In [88]:
result = pd.DataFrame()
result = pd.merge(result, df_result_a2c, how='outer', left_index=True, right_index=True)
result = pd.merge(result, df_result_ddpg, how='outer', left_index=True, right_index=True)
result = pd.merge(result, df_result_td3, how='outer', left_index=True, right_index=True)
result = pd.merge(result, df_result_ppo, how='outer', left_index=True, right_index=True)
result = pd.merge(result, df_result_sac, how='outer', left_index=True, right_index=True)
result = pd.merge(result, df_dji, how='outer', left_index=True, right_index=True)
display(result)

a2c          ddpg           td3           ppo  \
date                                                                 
2021-10-01  1.000000e+06  1.000000e+06  1.000000e+06  1.000000e+06   
2021-10-04  9.974116e+05  9.976737e+05  9.972112e+05  9.998214e+05   
2021-10-05  1.001676e+06  1.001038e+06  1.002644e+06  1.000013e+06   
2021-10-06  1.004536e+06  1.002284e+06  1.005675e+06  1.000121e+06   
2021-10-07  1.013392e+06  1.009239e+06  1.017347e+06  1.000458e+06   
...                  ...           ...           ...           ...   
2023-02-21  1.107141e+06  1.037949e+06  1.072328e+06  9.939497e+05   
2023-02-22  1.106296e+06  1.034718e+06  1.067711e+06  9.946200e+05   
2023-02-23  1.108018e+06  1.039800e+06  1.072953e+06  9.964375e+05   
2023-02-24  1.099715e+06  1.029044e+06  1.066027e+06  9.873245e+05   
2023-02-27  1.103832e+06  1.034149e+06  1.066999e+06  9.869171e+05   

                     sac           dji  
date                                    
2021-10-01  1.000000e+06  1.000000e+06  
2021-10-04  9.980301e+05  9.905746e+05  
2021-10-05  1.001900e+06  9.996566e+05  
2021-10-06  1.003205e+06  1.002637e+06  
2021-10-07  1.008505e+06  1.012483e+06  
...                  ...           ...  
2023-02-21  9.867896e+05  9.651327e+05  
2023-02-22  9.845209e+05  9.626710e+05  
2023-02-23  9.868170e+05  9.658412e+05  
2023-02-24  9.785792e+05  9.560240e+05  
2023-02-27  9.810789e+05  9.581264e+05  

[353 rows x 6 columns]

Save and Plot!

In [89]:
plt.rcParams["figure.figsize"] = (15,5)
plt.figure();
result.plot();
plt.savefig(f'resultadosTFG/set_3/AlgorithmsVsDJI.png')
plt.close()